In [1]:
!python --version

Python 3.10.12


In [2]:
!pip install torch torchvision torchaudio

In [3]:
!pip install Cython

In [4]:
!pip install nemo_toolkit['all']

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.7/15.7 MB 45.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.4/116.4 kB 4.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.5/97.5 kB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.6/97.6 kB 4.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.3/92.3 kB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.9/40.9 kB 3.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 19.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.5/154.5 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.5/79.5 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 725.0/725.0 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 806.1/806.1 kB 12.5 MB/s eta 

In [5]:
# !wget -O checkpoint.ckpt "https://vnueduvn-my.sharepoint.com/:u:/g/personal/21020205_vnu_edu_vn/EbYkGgMABVBFg3oiM9iWA3MBnjmxvVIJJ-5BEDUwJ7w7LQ?e=uwmuCM&download=1"

In [9]:
# !wget -O checkpoint.ckpt "https://vnueduvn-my.sharepoint.com/:u:/g/personal/21020108_vnu_edu_vn/Ef7m8t9hPMtPkkmP53dFnpEBXhFsC6HzOIO3bjD_actStw?e=ThGyC6&download=1"
!wget -O mymodel.nemo https://vnueduvn-my.sharepoint.com/:u:/g/personal/21020108_vnu_edu_vn/ETWXfO-Sh3FHpChCw0V-POgBjOEjXXsaKeDKGcK0nO9_8g?e=ddoyP9&download=1

--2023-12-18 02:46:48--  https://vnueduvn-my.sharepoint.com/:u:/g/personal/21020108_vnu_edu_vn/ETWXfO-Sh3FHpChCw0V-POgBjOEjXXsaKeDKGcK0nO9_8g?e=ddoyP9
Resolving vnueduvn-my.sharepoint.com (vnueduvn-my.sharepoint.com)... 13.107.136.10, 13.107.138.10, 2620:1ec:8f8::10, ...
Connecting to vnueduvn-my.sharepoint.com (vnueduvn-my.sharepoint.com)|13.107.136.10|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://vnueduvn-my.sharepoint.com/personal/21020108_vnu_edu_vn/_layouts/15/onedrive.aspx?id=%2Fpersonal%2F21020108%5Fvnu%5Fedu%5Fvn%2FDocuments%2Fmymodel%2Enemo&parent=%2Fpersonal%2F21020108%5Fvnu%5Fedu%5Fvn%2FDocuments&ga=1 [following]
--2023-12-18 02:46:49--  https://vnueduvn-my.sharepoint.com/personal/21020108_vnu_edu_vn/_layouts/15/onedrive.aspx?id=%2Fpersonal%2F21020108%5Fvnu%5Fedu%5Fvn%2FDocuments%2Fmymodel%2Enemo&parent=%2Fpersonal%2F21020108%5Fvnu%5Fedu%5Fvn%2FDocuments&ga=1
Reusing existing connection to vnueduvn-my.sharepoint.com:443.
HTTP request 

In [7]:
import os
try:
    from ruamel.yaml import YAML
except ModuleNotFoundError:
    from ruamel_yaml import YAML

# NeMo's "core" package
import nemo
# NeMo's ASR collection - this collections contains complete ASR models and
# building blocks (modules) for ASR
import nemo.collections.asr as nemo_asr
from omegaconf import DictConfig
import copy
import pytorch_lightning as pl
import torch

In [16]:
class RunModel:
    def __init__(self) -> None:
        self.model = nemo_asr.models.EncDecCTCModel.load_from_checkpoint("checkpoint.ckpt", map_location='cpu')
        # self.model = nemo_asr.models.EncDecCTCModel.load_from_checkpoint(checkpoint_path="mymodel.nemo")

    def get_result(self, path2audio_files) :
        batch_sz = 4
        trans = []
        batch = []
        for i in range(len(path2audio_files)) :
            batch.append(path2audio_files[i])
            if (i % batch_sz == batch_sz - 1) :
                rt = self.model.transcribe(paths2audio_files=batch, batch_size=len(batch))
                for _ in rt:
                    trans.append(_)
                batch = []
        rt = self.model.transcribe(paths2audio_files=batch, batch_size=len(batch))
        for _ in rt:
            trans.append(_)
        # return model.transcribe(paths2audio_files=path2audio_files, batch_size=len(path2audio_files))
        return trans
    def save_model(self):
        self.model.save_to(save_path="mymodel.nemo")

model = RunModel()
# model.save_model()

[NeMo W 2023-12-18 02:48:25 modelPT:161] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: /work/hpc/potato/asr/data/LibriSpeech/dev-clean_manifest.json
    sample_rate: 16000
    labels:
    - ' '
    - a
    - b
    - c
    - d
    - e
    - f
    - g
    - h
    - i
    - j
    - k
    - l
    - m
    - 'n'
    - o
    - p
    - q
    - r
    - s
    - t
    - u
    - v
    - w
    - x
    - 'y'
    - z
    - ''''
    batch_size: 16
    trim_silence: true
    max_duration: 16.7
    shuffle: true
    num_workers: 8
    pin_memory: true
    is_tarred: false
    tarred_audio_filepaths: null
    shuffle_n: 2048
    bucketing_strategy: synced_randomized
    bucketing_batch_size: null
    
[NeMo W 2023-12-18 02:48:25 modelPT:168] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_mult

[NeMo I 2023-12-18 02:48:25 features:289] PADDING: 16


In [17]:
!pip install flask-ngrok
!pip install pyngrok==4.1.1
!pip install flask[async]
!ngrok authtoken 2ZDpxzhxZP7h0QMThOw4FJkJrIS_3DCv44LHYHKX1jNNMzVn8

  Preparing metadata (setup.py) ... done
  Created wheel for pyngrok: filename=pyngrok-4.1.1-py3-none-any.whl size=15963 sha256=0f73292835ac0c11986ce59ae2207d6e6b5c6546b9e801b6abf5c7e95b9ff965
  Stored in directory: /root/.cache/pip/wheels/4c/7c/4c/632fba2ea8e88d8890102eb07bc922e1ca8fa14db5902c91a8
Successfully built pyngrok
Authtoken saved to configuration file: /root/.ngrok2/ngrok.yml


In [18]:
!apt-get install sox

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  libopencore-amrnb0 libopencore-amrwb0 libsox-fmt-alsa libsox-fmt-base libsox3 libwavpack1
Suggested packages:
  libsox-fmt-all
The following NEW packages will be installed:
  libopencore-amrnb0 libopencore-amrwb0 libsox-fmt-alsa libsox-fmt-base libsox3 libwavpack1 sox
0 upgraded, 7 newly installed, 0 to remove and 24 not upgraded.
Need to get 617 kB of archives.
After this operation, 1,764 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 libopencore-amrnb0 amd64 0.1.5-1 [94.8 kB]
Get:2 http://archive.ubuntu.com/ubuntu jammy/universe amd64 libopencore-amrwb0 amd64 0.1.5-1 [49.1 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 libsox3 amd64 14.4.2+git20190427-2+deb11u2ubuntu0.22.04.1 [240 kB]
Get:4 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 libs

In [19]:
# !pip install aiohttp[speedups]
# !pip install nest_asyncio

In [20]:
import soundfile as sf
import numpy as np
import librosa

In [21]:
def split_wav(input_path, output_folder, segment_duration=10):
    y, sr = librosa.load(input_path, sr=None)

    segment_frames = int(segment_duration * sr)
    files = []

    for i in range(0, len(y), segment_frames):
        segment = y[i:i+segment_frames]
        output_file = f"{output_folder}/segment_{i // segment_frames + 1}.wav"
        sf.write(file=output_file, data=segment, samplerate=sr)
        files.append(output_file)
    return files

In [22]:
!mkdir divided

In [23]:
# input_path = "/content/xltn_team6/test10p.wav"
# output_folder = "/content/divided3"
# split_wav(input_path, output_folder)

def solve_a_file(input_path):
    split = split_wav(input_path, "divided")
    ans = model.get_result(split)
    rt = ""
    for x in ans:
        rt = rt + x + " "
    return (rt, input_path)

In [24]:
def split_many_file(input_paths):
    paths = []
    for p in input_paths:
        p.save(p.filename)
        path = solve_a_file(p.filename)
        paths.append(path)
    return paths

In [25]:
from flask import Flask, request
from flask_ngrok import run_with_ngrok
import subprocess
from io import StringIO

In [33]:
app = Flask(__name__)
run_with_ngrok(app)

@app.route("/")
async def home():
    return """
        <h1>Please choose the audio file:</h1>
        <h3>Allowed audio file types: .wav</h3>
        <form action="/uploader" method="POST" enctype = "multipart/form-data">
            <input type = "file" name = "file" multiple/>
            <br>
            <input type = "submit"/>
        </form>
        <br>
        <p id="return"></p>
        """

# def process_file(files) :
#       # files = split_many_file(files)
#       path = []
#       duration = []
#       for file in files:
#           parts = file.filename.split(".")
#           if parts[-1] != "wav":
#               return "Not wav file"
#           local_filename = "flask_" + file.filename
#           print(local_filename)
#           file.save(local_filename)
#           path.append("/content/" + local_filename)
#           output = float(subprocess.check_output(['sox', '--i', '-D', local_filename]))
#           duration.append(output)
#       output = model.get_result(path)
#       ans = 'file uploaded successfully <br>'
#       for idx in range(len(output)):
#           ans = ans + "{text: " +  output[idx] + ", duration: " + str(duration[idx]) + "}" +  "<br>"
#       return ans

def process_file(files) :
      files = split_many_file(files)
      filename = []
      output = []
      duration = []
      for (plot, fi) in files:
          # filename = file.split('/')
          filename.append(fi)
          output.append(plot)
          durex = float(subprocess.check_output(['sox', '--i', '-D', fi]))
          duration.append(durex)
      # output = model.get_result(files)
      # print(len(output))
      ans = 'file uploaded successfully <br>'
      for idx in range(len(output)):
          ans = ans + "<li> file: " + filename[idx] + ", text: " +  output[idx] + ", duration: " + str(duration[idx]) + "s. </li>" +  "<br>"
      return ans

import time

@app.route('/uploader', methods = ['GET', 'POST'])
async def upload_file():
   if request.method == 'POST':
      # async with aiohttp.ClientSession("/") as session:
      #     async with session.get('/') as resp:
      #         print(resp.status)
      #         print(await resp.text())
      start_time = time.time()
      f = request.files.getlist('file')
      ans = process_file(f)
      duration = time.time() - start_time
      ans = ans + "<br>Duration: " + str(duration) + "s. <br><a href='/'>Back</a>"
      return ans

app.run()

 * Serving Flask app '__main__'
 * Debug mode: off


INFO:werkzeug:WARNING: This is a development server. Do not use it in a production deployment. Use a production WSGI server instead.
 * Running on http://127.0.0.1:5000
INFO:werkzeug:Press CTRL+C to quit


 * Running on http://498f-34-132-76-96.ngrok-free.app
 * Traffic stats available on http://127.0.0.1:4040


INFO:werkzeug:127.0.0.1 - - [18/Dec/2023 02:51:53] "GET / HTTP/1.1" 200 -
INFO:werkzeug:127.0.0.1 - - [18/Dec/2023 02:51:53] "GET /favicon.ico HTTP/1.1" 404 -


Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

...

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

INFO:werkzeug:127.0.0.1 - - [18/Dec/2023 02:54:30] "POST /uploader HTTP/1.1" 200 -


In [35]:
def run_test_file(args):
    st_time = time.time()
    ans = []
    for x in args:
        ans.append(solve_a_file(x))
    # (word, fi) = solve_a_file(args)
    duration = time.time() - st_time
    rt = "Run time: " + str(duration) + "s\nResult:\n"
    for (word, fi) in ans:
        rt = rt + "File: " + fi + ", result: " + word + "\n"
    return rt

In [28]:
# !wget -O test10p.wav https://vnueduvn-my.sharepoint.com/:u:/g/personal/21020108_vnu_edu_vn/EWzsJjh09_pNlZLd5dzEKJIBe9KaYTSVeC3ScoA0Z_mNug?nav=eyJyZWZlcnJhbEluZm8iOnsicmVmZXJyYWxBcHAiOiJPbmVEcml2ZUZvckJ1c2luZXNzIiwicmVmZXJyYWxBcHBQbGF0Zm9ybSI6IldlYiIsInJlZmVycmFsTW9kZSI6InZpZXciLCJyZWZlcnJhbFZpZXciOiJNeUZpbGVzTGlua0NvcHkifX0&e=5CfAx9&download=1

--2023-12-18 02:50:43--  https://vnueduvn-my.sharepoint.com/:u:/g/personal/21020108_vnu_edu_vn/EWzsJjh09_pNlZLd5dzEKJIBe9KaYTSVeC3ScoA0Z_mNug?nav=eyJyZWZlcnJhbEluZm8iOnsicmVmZXJyYWxBcHAiOiJPbmVEcml2ZUZvckJ1c2luZXNzIiwicmVmZXJyYWxBcHBQbGF0Zm9ybSI6IldlYiIsInJlZmVycmFsTW9kZSI6InZpZXciLCJyZWZlcnJhbFZpZXciOiJNeUZpbGVzTGlua0NvcHkifX0
Resolving vnueduvn-my.sharepoint.com (vnueduvn-my.sharepoint.com)... 13.107.136.10, 13.107.138.10, 2620:1ec:8f8::10, ...
Connecting to vnueduvn-my.sharepoint.com (vnueduvn-my.sharepoint.com)|13.107.136.10|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://vnueduvn-my.sharepoint.com/personal/21020108_vnu_edu_vn/_layouts/15/stream.aspx?id=%2Fpersonal%2F21020108%5Fvnu%5Fedu%5Fvn%2FDocuments%2Ftest10p%2Ewav&nav=eyJyZWZlcnJhbEluZm8iOnsicmVmZXJyYWxBcHAiOiJPbmVEcml2ZUZvckJ1c2luZXNzIiwicmVmZXJyYWxBcHBQbGF0Zm9ybSI6IldlYiIsInJlZmVycmFsTW9kZSI6InZpZXciLCJyZWZlcnJhbFZpZXciOiJNeUZpbGVzTGlua0NvcHkifX0&nav=eyJyZWZlcnJhbEluZm8iOnsicmVmZXJyYWx

In [36]:
def test():
    # test 10-minute file:
    rt = "Test 10-minute file:\n"
    rt = rt + run_test_file(['test10p.wav']) + "\n"
    rt = rt + "Test 500 files:\n"
    arr = []
    for i in range(500):
        arr.append("test10p.wav")
    rt = rt + run_test_file(arr)
    f = open("test.log", "w")
    f.write(rt)
    f.close()

In [37]:
test()

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

...

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

In [38]:
!cat test.log

Test 10-minute file:
Run time: 106.36418032646179s
Result:
File: test10p.wav, result:  our lives are made up of small moments and small decisions left or right walk or drive eat in or take out lend a helping hand or some words of encouragement or an offer of support to a neighbor a colleague a stranger some of these decisions are not like the others and with the world in this much pain it might seem futile to be focussing on those kinds of miprodecisions trth is that we underestimate the power of our own generous actions every time we intentionally chee  generosity the effects of that choice are more powerful and more far reaching than we might think the true that what one person cant accomplish is enormous i've been one of the many leaders retting hem here in this room tuesday since it was created in two thousand twelve and it began as an experiment uh could we use social media to create t hay  of giving following two days of consumption by friday and cyber monday here in the u s and 